In [1]:
import datetime
import pandas as pd
import requests
from bs4 import BeautifulSoup

tenors=['01M', '03M','06M','01Y','02Y','03Y','05Y','07Y','10Y','30Y']
headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.116 Safari/537.36'}
bond_headers=['Date', 'Open','High','Low','Close']
bond_table_list=[]

for i, tenor in enumerate(tenors):

    url1 = "https://www.wsj.com/market-data/quotes/bond/BX/TMUBMUSD" + tenor + "?mod=md_bond_overview_quote"
    req = requests.get(url1,headers=headers)
    html = req.text
    soup = BeautifulSoup(html,'html.parser')

    date = soup.select('span[id=quote_dateTime]')
    yield_data = soup.select('span[id=quote_val]')

    dt = datetime.datetime.strptime(date[0].text[-8:], "%m/%d/%y")
    # dt = 2020-07-07
    # 7
    # 7
    # 2020
    # print(date[0].text)
    month=str(dt.month).zfill(2)
    day=str(dt.day).zfill(2)
    year=str(dt.year)

    url2='https://www.wsj.com/market-data/quotes/ajax/historicalpricesbond/8/'\
        'TMUBMUSD'+tenor+'?MOD_VIEW=page&ticker=TMUBMUSD'+tenor+'&country=BX&exchange=XTUP'\
        '&instrumentType=BOND&num_rows=20000&range_days=20000&startDate=03%2F01%2F2006&endDate='+month+'%2F'+day+'%2F'+year
    req = requests.get(url2,headers=headers)
    html = req.text
    historical_price = BeautifulSoup(html,'html.parser')

    bond_table =  historical_price.find_all('tbody')
    bond_rows = bond_table[0].select('tr')

    bond_content = []
    bond_contents = []

    for bond_row in bond_rows:
        tds = bond_row.find_all("td")
        for td in tds:
            bond_content.append(td.text)
        bond_content[0]=datetime.datetime.strptime(bond_content[0],"%m/%d/%y")
        bond_contents.append(bond_content)
        bond_content=[]

    bond_df=pd.DataFrame(bond_contents)
    bond_df.columns=bond_headers
    bond_df.set_index('Date',inplace=True)

    bond_table_list.append(bond_df)
    # print(bond_table_list[i].head(5))
    # print('\n\n\n')

In [2]:
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

# print(bond_table_list[0]['Close'])
# print(bond_table_list[0].index)

data_total=[]
# Plotting
for i, tenor in enumerate(tenors):
    trace = go.Scatter(x=bond_table_list[i].index, y=bond_table_list[i]['Close'], name=('Tenor = '+ tenor)) 
    layout = go.Layout( title='Dyanmic Visualization of historical data of '+ tenor +'\'s Bond', 
                        xaxis=dict( 
                            rangeselector=dict( 
                                buttons=list(
                                    [ dict(count=1, label='1m', step='month', stepmode='backward'), 
                                        dict(count=3, label='3m', step='month', stepmode='backward'), 
                                        dict(count=6, label='6m', step='month', stepmode='backward'), 
                                        dict(count=1, label="YTD", step="year", stepmode="todate"),
                                        dict(count=1, label="1y",step="year", stepmode="backward"),
                                        dict(count=2, label="2y",step="year", stepmode="backward"),
                                        dict(count=3, label="3y",step="year", stepmode="backward"),
                                        dict(count=5, label="5y",step="year", stepmode="backward"),
                                        dict(count=7, label="7y",step="year", stepmode="backward"),
                                        dict(count=10, label="10y",step="year", stepmode="backward"),
                                        dict(count=30, label="30y",step="year", stepmode="backward"),
                                        dict(step='all') ]) 
                                    ), 
                            rangeslider=dict(visible=True), 
                            type='date',
                            title='Date'
                            ),
                        yaxis=dict(title='Yield'),
                        width=800, height=600
                        )

    data1=[trace] 
    fig1 = dict(data=data1, layout=layout)
    iplot(fig1)
    data_total.append(trace)

In [3]:
# Plotting join together

layout_total = go.Layout(width=1000, height=700, xaxis=dict( 
                            rangeselector=dict( 
                                buttons=list(
                                    [ dict(count=1, label='1m', step='month', stepmode='backward'), 
                                        dict(count=3, label='3m', step='month', stepmode='backward'), 
                                        dict(count=6, label='6m', step='month', stepmode='backward'), 
                                        dict(count=1, label="YTD", step="year", stepmode="todate"),
                                        dict(count=1, label="1y",step="year", stepmode="backward"),
                                        dict(count=2, label="2y",step="year", stepmode="backward"),
                                        dict(count=3, label="3y",step="year", stepmode="backward"),
                                        dict(count=5, label="5y",step="year", stepmode="backward"),
                                        dict(count=7, label="7y",step="year", stepmode="backward"),
                                        dict(count=10, label="10y",step="year", stepmode="backward"),
                                        dict(count=30, label="30y",step="year", stepmode="backward"),
                                        dict(step='all') ]) 
                                    ), 
                            rangeslider=dict(visible=True), 
                            type='date',
                            title='Date'
                            ),
                        yaxis=dict(title='Yield'))
fig_total = dict(data=data_total, layout=layout_total)
iplot(fig_total)